# Classification Analysis
This notebook will contain classification analysis for both the sensed and pipelined algorithms. Analysis will be preformed in regards for the sensed and pipelined algorthms themselves, as well as the ensemble algorithms. The analysis for the ensemble algorithm will focus on the HAMF android phones and the HAHF iOS phones.

## Dependencies

In [1]:
# for reading and validating data
import emeval.input.spec_details as eisd
import emeval.input.phone_view as eipv
import emeval.input.eval_view as eiev

In [2]:
import emeval.viz.phone_view as ezpv
import emeval.viz.eval_view as ezev
import emeval.viz.geojson as ezgj

In [3]:
# for analysized view
import emeval.analysed.phone_view as eapv

In [4]:
import emeval.metrics.segmentation as ems

In [5]:
# Metrics helpers
import emeval.metrics.dist_calculations as emd
import emeval.metrics.reference_trajectory as emr

In [6]:
import pandas as pd
pd.options.display.float_format = '{:.6f}'.format
import arrow

In [7]:
import numpy as np
import scipy as sp
import scipy.interpolate
import scipy.integrate

In [8]:
# For plots
import matplotlib.pyplot as plt
%matplotlib inline

In [9]:
# For maps
import geopandas as gpd
import shapely as shp
import folium
import branca.element as bre

In [10]:
# For easier debugging while working on modules
import importlib

In [11]:
import arrow

In [12]:
def import_sd_and_pv_from_server(trips  = ["unimodal_trip_car_bike_mtv_la", "car_scooter_brex_san_jose", "train_bus_ebike_mtv_ucb"], 
                                 AUTHOR_EMAIL  = "shankari@eecs.berkeley.edu", 
                                 DATASTORE_LOC = "http://localhost:8080", 
                                 pkl_file_name = None):
    sd_l = []
    pv_l = []
    for trip in trips:
        sd = eisd.ServerSpecDetails(DATASTORE_LOC, AUTHOR_EMAIL, trip)
        pv = eipv.PhoneView(sd)
        sd_l.append(sd)
        pv_l.append(pv)
    if pkl_file_name:
        import pickle
        with open(pkl_file_name, 'wb') as outp:
            for pv in pv_l:
                pickle.dump(pv, outp, pickle.HIGHEST_PROTOCOL)
    return sd_l, pv_l

In [13]:
def import_pv_from_pkl(pkl_file_name, 
                       trips = ["unimodal_trip_car_bike_mtv_la", "car_scooter_brex_san_jose", "train_bus_ebike_mtv_ucb"]):
    import pickle
    pv_l = []
    with open('pv.pkl', 'rb') as inp:
        for trip in trips:
            pv_l.append(pickle.load(inp))
    return pv_l

In [14]:
(pv_la, pv_sj, pv_ucb) = import_pv_from_pkl('pv.pkl')

### Get the sensed data for each trip

In [15]:
%%capture
ems.fill_sensed_section_ranges(pv_la)
ems.fill_sensed_section_ranges(pv_sj)
ems.fill_sensed_section_ranges(pv_ucb)

## Get sensed timeline

In [22]:
def get_trip_ss_and_gts_timeline(pv, os, role):
    assert os in ['android', 'ios'], 'UNKNOWN OS'
    assert role in ['accuracy_control', 'HAHFDC', 'HAMFDC', 'MAHFDC', 'power_control'], "UNKNOWN ROLE"
    trips = []
    for phone_os, phone_map in pv.map().items():
        if os != phone_os:
            continue
        for phone_label, phone_detail_map in phone_map.items():
            if "control" in phone_detail_map["role"]:
                continue
            for r in phone_detail_map["evaluation_ranges"]:
                if r['eval_role_base'] != role:
                    continue
                for tr in r["evaluation_trip_ranges"]:
                    tr_ss  = []
                    tr_gts = []
                    for ss in tr["sensed_section_ranges"]:
                        tr_ss.append(ss)
                    for section in tr["evaluation_section_ranges"]:
                        section_gt_leg = pv.spec_details.get_ground_truth_for_leg(tr['trip_id_base'],
                                                                                  section['trip_id_base'],
                                                                                  tr['start_ts'],
                                                                                  tr['end_ts'])
                        
                        if section_gt_leg["type"] == "WAITING":
                            continue
                        gts = {'start_ts': section['start_ts'], 
                               'end_ts': section['end_ts'], 
                               'mode': section_gt_leg['mode']}
                        tr_gts.append(gts)
                    # now, we build a timeline for each trip
                    trip = tr.copy()
                    trip['ss_timeline']  = tr_ss
                    trip['gts_timeline'] = tr_gts
                    trips.append(trip)
    return trips

## Binary Classification (in seconds)

#### rab base mode map

In [16]:
RBMM = {     "WALKING": "WALKING",
             "RUNNING" : "WALKING", 
             "CYCLING" : "CYCLING",
             "BICYCLING": "CYCLING",
             "ESCOOTER": "CYCLING", 
             "AUTOMOTIVE" : "AUTOMOTIVE",
             "BUS": "AUTOMOTIVE",
             "TRAIN": "AUTOMOTIVE",
             "LIGHT_RAIL": "AUTOMOTIVE",
             "SUBWAY": "AUTOMOTIVE",
             "CAR": "AUTOMOTIVE",
             "AIR_OR_HSR": "AUTOMOTIVE",
             "INVALID" : "INVALID"}

#### cleaned base mode map

e-mission-server.emission.core.wrapper.motionactivity.py

In [17]:
CBMM = {0 : 'AUTOMOTIVE', 
        1 : 'CYCLING', 
        2 : 'WALKING', 
        3 : 'WALKING', 
        4 : 'INVALID', 
        5 : 'WALKING', 
        7 : 'WALKING', 
        8 : 'WALKING', 
        9 : 'INVALID', 
        10 : 'AUTOMOTIVE', 
        11 : 'AUTOMOTIVE', 
         "WALKING": "WALKING",
         "RUNNING" : "WALKING", 
         "CYCLING" : "CYCLING",
         "BICYCLING": "CYCLING",
         "ESCOOTER": "CYCLING", 
         "AUTOMOTIVE" : "AUTOMOTIVE",
         "BUS": "AUTOMOTIVE",
         "TRAIN": "AUTOMOTIVE",
         "LIGHT_RAIL": "AUTOMOTIVE",
         "SUBWAY": "AUTOMOTIVE",
         "CAR": "AUTOMOTIVE",
         "AIR_OR_HSR": "AUTOMOTIVE",
         "INVALID" : "INVALID"}

#### inferred base mode map

e-mission-server.emission.core.wrapper.modeprediction.py

In [18]:
IBMM = {0 : 'INVALID', 
        1 : 'WALKING', 
        2 : 'CYCLING', 
        3 : 'AUTOMOTIVE', 
        4 : 'TRAIN', 
        5 : 'AUTOMOTIVE', 
        6 : 'AUTOMOTIVE', 
         "WALKING": "WALKING",
         "RUNNING" : "WALKING", 
         "CYCLING" : "CYCLING",
         "BICYCLING": "CYCLING",
         "ESCOOTER": "CYCLING", 
         "AUTOMOTIVE" : "AUTOMOTIVE",
         "BUS": "AUTOMOTIVE",
         "TRAIN": "TRAIN",
         "LIGHT_RAIL": "TRAIN",
         "SUBWAY": "TRAIN",
         "CAR": "AUTOMOTIVE",
         "AIR_OR_HSR": "TRAIN",
         "INVALID" : "INVALID"}

### Align the GTS timeline with SS timeline

In [208]:
# det align_gts(trips)
trips = get_trip_ss_and_gts_timeline(cv_la, 'ios', 'HAHFDC')
for trip in trips:
    for gts in trip['gts_timeline']:
        
        for ss in trip['ss_timeline']:
            if 'data' in ss.keys():
                ss = ss['data']
                ss['mode'] = ss['sensed_mode']
                ss['data']['distances']
            if ss['start_ts'] <= gts['start_ts'] <= ss['end_ts']:
                
                mesh = np.linspace(ss['start_ts'], ss['end_ts'], len(ss['distances']) - 1, endpoint=False)
                print(np.abs(mesh - gts['start_ts']).min())
                nearest = (np.abs(mesh - gts['start_ts']).argmin())
                snapped_start_ts = mesh[nearest]
#                 print(snapped_start_ts - gts['start_ts'])

7.1363348960876465
10.066160678863525
10.089910984039307
20.201975345611572
7.033864974975586
7.8322529792785645
8.252450466156006
6.201812028884888
6.284194469451904
1.4199345111846924


In [158]:
def get_binary_class_in_sec(os, role, pv, BASE_MODE):
    if type(pv) is not list: pv = [pv]
    trips = []
    for v in pv:
        trips.extend(get_trip_ss_and_gts_timeline(v, os, role))
    TP, FN, FP, TN = {}, {}, {}, {}
    for trip in trips:
        for mode in set(BASE_MODE.values()):
            for ss in trip['ss_timeline']:
                if 'data' in ss.keys():
                    ss = ss['data']
                    ss['mode'] = ss['sensed_mode']
                x = np.linspace(ss['start_ts'], ss['end_ts'], len(ss['distances']))
                ss_dist  = np.array(ss['distances']).sum()
                comp_dist = 0
                for gts in trip['gts_timeline']:  
                    dist = 0
                    if gts['start_ts'] <= ss['start_ts'] and ss['end_ts'] <= gts['end_ts']:
                        dist = ss_dist
                        comp_dist += dist
                    elif ss['end_ts'] >= gts['start_ts'] and ss['start_ts'] <= gts['end_ts']:
                       
                        a = max(ss['start_ts'], gts['start_ts'])
                        b = min(ss['end_ts'], gts['end_ts'])
                        start_idx = int(len(ss['distances']) * (1 - (ss['end_ts']-a)/ ss['duration']))
                        stop_idx = int((b-ss['start_ts'])/ ss['duration'] * len(ss['distances']))+ 1
                        dist = np.array(ss['distances'])[start_idx:stop_idx].sum()
                        assert dist >= 0, f"{dist}"
                        comp_dist += dist
                    if BASE_MODE[mode] == BASE_MODE[ss['mode']] and BASE_MODE[mode] == BASE_MODE[gts['mode']]:
                        TP[mode] = TP.setdefault(mode, 0) + dist
                    elif BASE_MODE[mode] == BASE_MODE[ss['mode']] and BASE_MODE[mode] != BASE_MODE[gts['mode']]:
                        FP[mode] = FP.setdefault(mode, 0) + dist
                    elif BASE_MODE[mode] != BASE_MODE[ss['mode']] and BASE_MODE[mode] == BASE_MODE[gts['mode']]:
                        FN[mode] = FN.setdefault(mode, 0) + dist
                    else:
                        TN[mode] = TN.setdefault(mode, 0) + dist

                leftover = ss_dist - comp_dist
                assert leftover >= -1e-10, f""" 
                ERROR, NEGATIVE LEFTOVER OF {leftover}, NEED TO INVESTIGATE
                sensed distance:   \t {ss_dist}
                computed distance: \t {comp_dist}
                mode:              \t {mode}
                                      """        
                if leftover > 0:
                    # invalid base mode maps to NO_GT mode
                    if mode == 'INVALID':
                        TP[mode] = TP.setdefault(mode, 0) + leftover
                    # We have no gts, but our modes are equal, so a false positive
                    elif BASE_MODE[mode] == BASE_MODE[ss['mode']]:
                        FP[mode] = FP.setdefault(mode, 0) + leftover
                    # We have no_gts, but our modes are unequal, so a true negative
                    else:
                        TN[mode] = TN.setdefault(mode, 0) + leftover
    return TP, FP, FN, TN

In [159]:
get_binary_class_in_sec('ios', 'HAHFDC', [cv_la, cv_sj, cv_ucb], CBMM)

{'source': 'SmoothedHighConfidenceMotion',
 'trip_id': {'$oid': '62c5f187f5cc6626fb67ff36'},
 'start_ts': 1564274906.0030518,
 'start_local_dt': {'year': 2019,
  'month': 7,
  'day': 27,
  'hour': 17,
  'minute': 48,
  'second': 26,
  'weekday': 5,
  'timezone': 'America/Los_Angeles'},
 'start_fmt_time': '2019-07-27T17:48:26.003052-07:00',
 'start_loc': {'type': 'Point',
  'coordinates': [-122.10434624936627, 37.378010898863316]},
 'end_ts': 1564275314.9845433,
 'end_local_dt': {'year': 2019,
  'month': 7,
  'day': 27,
  'hour': 17,
  'minute': 55,
  'second': 14,
  'weekday': 5,
  'timezone': 'America/Los_Angeles'},
 'end_fmt_time': '2019-07-27T17:55:14.984543-07:00',
 'end_loc': {'type': 'Point',
  'coordinates': [-122.11342980165232, 37.38074314784014]},
 'duration': 408.98149156570435,
 'speeds': [0.0,
  9.966008918173669,
  4.8896155734511115,
  6.722831181347224,
  7.638657136479184,
  2.1879031669526214,
  5.732121194849811,
  2.9411564614992756,
  0.4351653982245738,
  0.179083

In [103]:
def get_binary_raw_data(os, pv, BMM):
    BASE_MODE = BMM
    df = pd.DataFrame(get_binary_class_in_sec(os, 'HAHFDC', pv, BASE_MODE)).fillna(0)
    df=df.reindex(columns=['WALKING', 'CYCLING', 'AUTOMOTIVE', 'INVALID'])
    dic={}
    d = df.reset_index(drop=True)
    dic['ios'+'\\_'+'HAHFDC'] = d
    d = pd.concat(dic, axis=1)
    d['Classifier'] = ['TP', 'FP', 'FN', 'TN']
    print(d.set_index('Classifier').rename_axis(['Title', 'Mode'], axis=1).astype(int).style.to_latex())
    df = pd.DataFrame(get_binary_class_in_sec(os, 'HAMFDC', pv, BASE_MODE)).fillna(0)
    df=df.reindex(columns=['WALKING', 'CYCLING', 'AUTOMOTIVE', 'INVALID'])
    dic={}
    d = df.reset_index(drop=True)
    dic['ios'+'\\_'+'HAHFDC'] = d
    d = pd.concat(dic, axis=1)
    d['Classifier'] = ['TP', 'FP', 'FN', 'TN']
    print(d.set_index('Classifier').rename_axis(['Title', 'Mode'], axis=1).astype(int).style.to_latex())
    df = pd.DataFrame(get_binary_class_in_sec(os, 'MAHFDC', pv, BASE_MODE)).fillna(0)
    df=df.reindex(columns=['WALKING', 'CYCLING', 'AUTOMOTIVE', 'INVALID'])
    dic={}
    d = df.reset_index(drop=True)
    dic['ios'+'\\_'+'HAHFDC'] = d
    d = pd.concat(dic, axis=1)
    d['Classifier'] = ['TP', 'FP', 'FN', 'TN']
    print(d.set_index('Classifier').rename_axis(['Title', 'Mode'], axis=1).astype(int).style.to_latex())

#### random forrest binary tables
BASE MODES = `['WALKING', 'CYCLING', 'AUTOMOTIVE', 'INVALID']`

In [104]:
def get_rf_binary(os, pv):
    BASE_MODE = IBMM
    for role in ['HAHFDC', 'HAMFDC', 'MAHFDC']:
        df = pd.DataFrame(get_binary_class_in_sec(os, role, pv, BASE_MODE)).fillna(0)
        df=df.reindex(columns=['WALKING', 'CYCLING', 'AUTOMOTIVE', 'TRAIN', 'INVALID'])
        dic={}
        d = df.reset_index(drop=True)
        dic[os+'\\_'+role] = d
        d = pd.concat(dic, axis=1)
        d['Classifier'] = ['TP', 'FP', 'FN', 'TN']
        print(d.set_index('Classifier').rename_axis(['Title', 'Mode'], axis=1).astype(int).style.to_latex())

# $F_\beta$ score
$$
F_\beta = \frac {(1 + \beta^2) \cdot \mathrm{true\ positive} }{(1 + \beta^2) \cdot \mathrm{true\ positive} + \beta^2 \cdot \mathrm{false\ negative} + \mathrm{false\ positive}}
$$

In [105]:
def get_F_score(os, role, pv, BASE_MODE, beta=1):
    assert os in ['android', 'ios'], 'UNKNOWN OS'
    assert role in ['accuracy_control', 'HAHFDC', 'HAMFDC', 'MAHFDC', 'power_control'], "UNKNOWN ROLE"
    (TP, FP, FN, TN) = get_binary_class_in_sec(os, role, pv, BASE_MODE)
    F_score = {}
    for mode in TP.keys():
        numerator   = (1 + beta**2) * TP.setdefault(mode, 0)
        denominator = (1+beta**2) * TP.setdefault(mode, 0) + beta**2*FN.setdefault(mode, 0) + FP.setdefault(mode, 0)
        F_score[mode] = (numerator)/(denominator)
    # initializing K 
    K = 10
    for key in F_score:

        # rounding to K using round()
        F_score[key] = round(F_score[key], K)
    return F_score

In [106]:
def display_f_score(os, pv, BASE_MODE):
    return ([ (k, round(get_F_score(os, 'HAHFDC', pv, BASE_MODE, beta=1)[k], 4)) for k in get_F_score(os, 'HAHFDC', pv, BASE_MODE, beta=1)],
            [ (k, round(get_F_score(os, 'HAMFDC', pv, BASE_MODE, beta=1)[k], 4)) for k in get_F_score(os, 'HAMFDC', pv, BASE_MODE, beta=1)],
            [ (k, round(get_F_score(os, 'MAHFDC', pv, BASE_MODE, beta=1)[k], 4)) for k in get_F_score(os, 'MAHFDC', pv, BASE_MODE, beta=1)],
            )

## Confusion Matrix
We will now generate confusion matrices based off OS and role, with the acctual modes as the rows, the predicted modes as the columns, and the entries as the base unit for the duration measurement

In [107]:
def get_confusion_matrix(os, role, pv):
    assert os in ['android', 'ios'], 'UNKNOWN OS'
    assert role in ['accuracy_control', 'HAHFDC', 'HAMFDC', 'MAHFDC', 'power_control'], "UNKNOWN ROLE"
    cm_l = []
    if type(pv) is not list:
        pv = [pv]
    trips = []
    for v in pv :
        trips.extend(get_trip_ss_and_gts_timeline(v, os, role))
    for trip in trips:
        for ss in trip['ss_timeline']:
            if 'data' in ss.keys():
                # taken from emission.core.wrapper.modeprediction
                ss = ss['data']
            
            ss_dur = ss['end_ts'] - ss['start_ts']
            gts_dur = 0
            cm = {}
            for gts in trip['gts_timeline']:
                dur = 0
                if ss['end_ts'] >= gts['start_ts'] and ss['start_ts'] <= gts['end_ts']:
                    dur = min(ss['end_ts'], gts['end_ts']) - max(ss['start_ts'], gts['start_ts'])
                    
                gts_dur += dur
                cm[gts['mode']] = cm.setdefault(gts['mode'], 0) + dur
            leftover = ss_dur - gts_dur
            assert leftover >= 0, f"ERROR, NEGATIVE LEFTOVER OF {leftover}, NEED TO INVESTIGATE"
            cm['NO_GT'] = cm.setdefault('NO_GT', 0) + leftover
            cm['sensed_mode'] = ss['mode']
            
            cm_l.append(cm)
    return cm_l

In [108]:
def get_raw_cm(os, pv):
    if os == 'ios':
        df = pd.DataFrame(get_confusion_matrix(os, 'HAHFDC', pv)).groupby('sensed_mode').sum().astype(int)
        print(df.reindex(columns=['WALKING', 'BICYCLING', 'ESCOOTER', 'CAR', 'BUS', 'LIGHT_RAIL', 'TRAIN', 'NO_GT'],
                   index=['WALKING', 'RUNNING', 'CYCLING', 'AUTOMOTIVE']).style.to_latex())
        df = pd.DataFrame(get_confusion_matrix(os, 'HAMFDC', pv)).groupby('sensed_mode').sum().astype(int)
        print(df.reindex(columns=['WALKING', 'BICYCLING', 'ESCOOTER','CAR', 'BUS', 'LIGHT_RAIL', 'TRAIN', 'NO_GT'],
                   index=['WALKING', 'RUNNING', 'CYCLING', 'AUTOMOTIVE']).style.to_latex())
        df = pd.DataFrame(get_confusion_matrix(os, 'MAHFDC', pv)).groupby('sensed_mode').sum().astype(int)
        print(df.reindex(columns=['WALKING', 'BICYCLING', 'ESCOOTER','CAR', 'BUS', 'LIGHT_RAIL', 'TRAIN', 'NO_GT'],
                   index=['WALKING', 'RUNNING', 'AUTOMOTIVE']).style.to_latex())
    if os == 'android':
        df = pd.DataFrame(get_confusion_matrix(os, 'HAHFDC', pv)).groupby('sensed_mode').sum().astype(int)
        print(df.reindex(columns=['WALKING', 'BICYCLING', 'ESCOOTER','CAR', 'BUS', 'LIGHT_RAIL', 'TRAIN', 'NO_GT'],
                   index=['WALKING', 'CYCLING', 'AUTOMOTIVE']).style.to_latex())
        df = pd.DataFrame(get_confusion_matrix(os, 'HAMFDC', pv)).groupby('sensed_mode').sum().astype(int)
        print(df.reindex(columns=['WALKING', 'BICYCLING', 'ESCOOTER','CAR', 'BUS', 'LIGHT_RAIL', 'TRAIN', 'NO_GT'],
                   index=['WALKING', 'CYCLING', 'AUTOMOTIVE']).style.to_latex())
        df = pd.DataFrame(get_confusion_matrix(os, 'MAHFDC', pv)).groupby('sensed_mode').sum().astype(int)
        print(df.reindex(columns=['WALKING', 'BICYCLING', 'ESCOOTER','CAR', 'BUS', 'LIGHT_RAIL', 'TRAIN', 'NO_GT'],
                   index=['WALKING', 'CYCLING', 'AUTOMOTIVE']).style.to_latex())

In [109]:
def get_rf_cm(os, BMM):
    if os == 'ios':
        df = pd.DataFrame(get_confusion_matrix('ios', 'HAHFDC', [rfv_la, rfv_sj, rfv_ucb])).groupby('sensed_mode').sum().astype(int)
        print(df.reindex(columns=['WALKING', 'BICYCLING', 'ESCOOTER', 'CAR', 'BUS', 'LIGHT_RAIL', 'TRAIN', 'NO_GT'],
                   index=['WALKING', 'BICYCLING', 'TRAIN', 'CAR', 'AIR_OR_HSR']).style.to_latex())
        df = pd.DataFrame(get_confusion_matrix('ios', 'HAMFDC', [rfv_la, rfv_sj, rfv_ucb])).groupby('sensed_mode').sum().astype(int)
        print(df.reindex(columns=['WALKING', 'BICYCLING', 'ESCOOTER', 'CAR', 'BUS', 'LIGHT_RAIL', 'TRAIN', 'NO_GT'],
                   index=['WALKING', 'BICYCLING', 'CAR', 'AIR_OR_HSR']).style.to_latex())
        df = pd.DataFrame(get_confusion_matrix('ios', 'MAHFDC', [rfv_la, rfv_sj, rfv_ucb])).groupby('sensed_mode').sum().astype(int)
        print(df.reindex(columns=['WALKING', 'BICYCLING', 'ESCOOTER', 'CAR', 'BUS', 'LIGHT_RAIL', 'TRAIN', 'NO_GT'],
                   index=['WALKING', 'BICYCLING', 'CAR']).style.to_latex())
    if os == 'android':
        df = pd.DataFrame(get_confusion_matrix('android', 'HAHFDC', [rfv_la, rfv_sj, rfv_ucb])).groupby('sensed_mode').sum().astype(int)
        print(df.reindex(columns=['WALKING', 'BICYCLING', 'ESCOOTER', 'CAR', 'BUS', 'LIGHT_RAIL', 'TRAIN', 'NO_GT'],
                   index=['WALKING', 'BICYCLING', 'CAR', 'AIR_OR_HSR']).style.to_latex())
        df = pd.DataFrame(get_confusion_matrix('android', 'HAMFDC', [rfv_la, rfv_sj, rfv_ucb])).groupby('sensed_mode').sum().astype(int)
        print(df.reindex(columns=['WALKING', 'BICYCLING', 'ESCOOTER', 'CAR', 'BUS', 'LIGHT_RAIL', 'TRAIN', 'NO_GT'],
                   index=['WALKING', 'BICYCLING', 'TRAIN', 'CAR']).style.to_latex())
        df = pd.DataFrame(get_confusion_matrix('android', 'MAHFDC', [rfv_la, rfv_sj, rfv_ucb])).groupby('sensed_mode').sum().astype(int)
        print(df.reindex(columns=['WALKING', 'BICYCLING', 'ESCOOTER', 'CAR', 'BUS', 'LIGHT_RAIL', 'TRAIN', 'NO_GT'],
                   index=['WALKING', 'BICYCLING', 'TRAIN', 'CAR', 'AIR_OR_HSR']).style.to_latex())

## Analyzed Data

#### cleaned view

In [20]:
cv_la   = eapv.create_analysed_view(pv_la, "http://localhost:8080", "analysis/recreated_location", "analysis/cleaned_trip", "analysis/cleaned_section")
cv_sj   = eapv.create_analysed_view(pv_sj, "http://localhost:8080", "analysis/recreated_location", "analysis/cleaned_trip", "analysis/cleaned_section")
cv_ucb  = eapv.create_analysed_view(pv_ucb, "http://localhost:8080", "analysis/recreated_location", "analysis/cleaned_trip", "analysis/cleaned_section")

Finished copying unimodal_trip_car_bike_mtv_la, starting overwrite
=*=*=*=*=*=*=*=*=*=*=*=*=*=*=*
android dict_keys(['ucb-sdb-android-1', 'ucb-sdb-android-2', 'ucb-sdb-android-3', 'ucb-sdb-android-4'])
     -*-*-*-*-*-*-*-*-*-*-*-*-*-*-*
     ucb-sdb-android-1 accuracy_control dict_keys(['role', 'manual/evaluation_transition', 'calibration_transitions', 'calibration_ranges', 'evaluation_transitions', 'evaluation_ranges'])
Retrieving data for ucb-sdb-android-1 from 1563606000 -> 1657287725.419432
Retrieving data for: post_body={'user': 'ucb-sdb-android-1', 'key_list': ['analysis/recreated_location'], 'start_time': 1563606000, 'end_time': 1657287725.419432}
response=<Response [200]>
Found 82 entries
Retrieving data for ucb-sdb-android-1 from 1657128596.112299 -> 1657287725.419432
Retrieving data for: post_body={'user': 'ucb-sdb-android-1', 'key_list': ['analysis/recreated_location'], 'start_time': 1657128596.112299, 'end_time': 1657287725.419432}
response=<Response [200]>
Found 1 entries

response=<Response [200]>
Found 3080 entries
Retrieving data for ucb-sdb-android-2 from 1657134290.4774148 -> 1657287725.833492
Retrieving data for: post_body={'user': 'ucb-sdb-android-2', 'key_list': ['analysis/recreated_location'], 'start_time': 1657134290.4774148, 'end_time': 1657287725.833492}
response=<Response [200]>
Found 1 entries
Retrieving data for ucb-sdb-android-2 from 1563606000 -> 1657287727.030205
Retrieving data for: post_body={'user': 'ucb-sdb-android-2', 'key_list': ['analysis/cleaned_trip'], 'start_time': 1563606000, 'end_time': 1657287727.030205}
response=<Response [200]>
Found 45 entries
Retrieving data for ucb-sdb-android-2 from 1657134288.8000069 -> 1657287727.030205
Retrieving data for: post_body={'user': 'ucb-sdb-android-2', 'key_list': ['analysis/cleaned_trip'], 'start_time': 1657134288.8000069, 'end_time': 1657287727.030205}
response=<Response [200]>
Found 1 entries
Retrieving data for ucb-sdb-android-2 from 1563606000 -> 1657287727.132758
Retrieving data for

response=<Response [200]>
Found 8992 entries
Retrieving data for ucb-sdb-android-3 from 1657138354.052344 -> 1657287727.42664
Retrieving data for: post_body={'user': 'ucb-sdb-android-3', 'key_list': ['analysis/recreated_location'], 'start_time': 1657138354.052344, 'end_time': 1657287727.42664}
response=<Response [200]>
Found 1 entries
Retrieving data for ucb-sdb-android-3 from 1563606000 -> 1657287730.236413
Retrieving data for: post_body={'user': 'ucb-sdb-android-3', 'key_list': ['analysis/cleaned_trip'], 'start_time': 1563606000, 'end_time': 1657287730.236413}
response=<Response [200]>
Found 124 entries
Retrieving data for ucb-sdb-android-3 from 1657138350.562826 -> 1657287730.236413
Retrieving data for: post_body={'user': 'ucb-sdb-android-3', 'key_list': ['analysis/cleaned_trip'], 'start_time': 1657138350.562826, 'end_time': 1657287730.236413}
response=<Response [200]>
Found 1 entries
Retrieving data for ucb-sdb-android-3 from 1563606000 -> 1657287730.390724
Retrieving data for: pos

Before filtering, trips = [('2019-06-19T14:13:32-07:00', '2019-06-19T14:41:05-07:00'), ('2019-06-21T11:48:53-07:00', '2019-06-21T11:56:31-07:00'), ('2019-06-21T15:29:54.764000-07:00', '2019-06-21T15:33:59-07:00'), ('2019-06-21T16:13:51.443866-07:00', '2019-06-21T16:20:33-07:00'), ('2019-06-21T16:24:42.645606-07:00', '2019-06-21T16:33:22.660000-07:00'), ('2019-06-21T16:33:22.660000-07:00', '2019-06-21T16:40:46.365000-07:00'), ('2019-06-21T16:40:46.365000-07:00', '2019-06-21T17:00:16-07:00'), ('2019-06-21T17:00:16-07:00', '2019-06-21T17:12:19-07:00'), ('2019-06-21T17:12:49-07:00', '2019-06-21T17:13:50-07:00'), ('2019-06-21T17:14:20-07:00', '2019-06-21T18:28:36-07:00'), ('2019-06-21T18:29:06-07:00', '2019-06-21T18:53:16.074000-07:00'), ('2019-07-12T10:05:51.634187-07:00', '2019-07-12T10:12:43-07:00'), ('2019-07-12T10:13:15-07:00', '2019-07-12T10:15:04-07:00'), ('2019-07-12T10:18:04.123513-07:00', '2019-07-12T10:20:24-07:00'), ('2019-07-18T16:03:30.668000-07:00', '2019-07-18T16:05:36-07:00

response=<Response [200]>
Found 1 entries
Retrieving data for ucb-sdb-android-4 from 1563606000 -> 1657287731.122398
Retrieving data for: post_body={'user': 'ucb-sdb-android-4', 'key_list': ['analysis/cleaned_trip'], 'start_time': 1563606000, 'end_time': 1657287731.122398}
response=<Response [200]>
Found 3 entries
Retrieving data for ucb-sdb-android-4 from 1657138578.899287 -> 1657287731.122398
Retrieving data for: post_body={'user': 'ucb-sdb-android-4', 'key_list': ['analysis/cleaned_trip'], 'start_time': 1657138578.899287, 'end_time': 1657287731.122398}
response=<Response [200]>
Found 1 entries
Retrieving data for ucb-sdb-android-4 from 1563606000 -> 1657287731.174514
Retrieving data for: post_body={'user': 'ucb-sdb-android-4', 'key_list': ['analysis/cleaned_section'], 'start_time': 1563606000, 'end_time': 1657287731.174514}
response=<Response [200]>
Found 5 entries
Retrieving data for ucb-sdb-android-4 from 1657138579.24949 -> 1657287731.174514
Retrieving data for: post_body={'user'

...

Before filtering, trips = [('2019-06-19T14:16:07.744506-07:00', '2019-06-19T14:42:28.989396-07:00'), ('2019-06-19T15:04:22.727851-07:00', '2019-06-19T15:11:59.984994-07:00'), ('2019-06-19T16:48:51.999810-07:00', '2019-06-19T17:01:27.989144-07:00'), ('2019-06-19T18:57:58.101197-07:00', '2019-06-19T19:12:42.997152-07:00'), ('2019-06-21T07:54:09.506301-07:00', '2019-06-21T08:03:10.996361-07:00'), ('2019-06-21T09:53:57.000253-07:00', '2019-06-21T10:06:55.986031-07:00'), ('2019-06-21T11:45:32.725421-07:00', '2019-06-21T11:58:56.483656-07:00'), ('2019-06-21T15:21:06.650344-07:00', '2019-06-21T15:49:12.452305-07:00'), ('2019-06-21T16:14:33.377063-07:00', '2019-06-21T16:32:19.962340-07:00'), ('2019-07-12T10:05:53.199050-07:00', '2019-07-12T10:12:52.990710-07:00'), ('2019-07-12T10:13:23.989402-07:00', '2019-07-12T10:13:57.987967-07:00'), ('2019-07-12T10:17:51.996739-07:00', '2019-07-12T10:25:23.995728-07:00'), ('2019-07-18T16:05:51.721434-07:00', '2019-07-18T16:18:22.989338-07:00'), ('2019-07-1

Before filtering, trips = [('2019-06-19T14:16:07.744506-07:00', '2019-06-19T14:42:28.989396-07:00'), ('2019-06-19T15:04:22.727851-07:00', '2019-06-19T15:11:59.984994-07:00'), ('2019-06-19T16:48:51.999810-07:00', '2019-06-19T17:01:27.989144-07:00'), ('2019-06-19T18:57:58.101197-07:00', '2019-06-19T19:12:42.997152-07:00'), ('2019-06-21T07:54:09.506301-07:00', '2019-06-21T08:03:10.996361-07:00'), ('2019-06-21T09:53:57.000253-07:00', '2019-06-21T10:06:55.986031-07:00'), ('2019-06-21T11:45:32.725421-07:00', '2019-06-21T11:58:56.483656-07:00'), ('2019-06-21T15:21:06.650344-07:00', '2019-06-21T15:49:12.452305-07:00'), ('2019-06-21T16:14:33.377063-07:00', '2019-06-21T16:32:19.962340-07:00'), ('2019-07-12T10:05:53.199050-07:00', '2019-07-12T10:12:52.990710-07:00'), ('2019-07-12T10:13:23.989402-07:00', '2019-07-12T10:13:57.987967-07:00'), ('2019-07-12T10:17:51.996739-07:00', '2019-07-12T10:25:23.995728-07:00'), ('2019-07-18T16:05:51.721434-07:00', '2019-07-18T16:18:22.989338-07:00'), ('2019-07-1

response=<Response [200]>
Found 206 entries
Retrieving data for ucb-sdb-ios-4 from 1657140407.6061382 -> 1657287819.846237
Retrieving data for: post_body={'user': 'ucb-sdb-ios-4', 'key_list': ['analysis/recreated_location'], 'start_time': 1657140407.6061382, 'end_time': 1657287819.846237}
response=<Response [200]>
Found 1 entries
Retrieving data for ucb-sdb-ios-4 from 1563260400 -> 1657287819.999794
Retrieving data for: post_body={'user': 'ucb-sdb-ios-4', 'key_list': ['analysis/cleaned_trip'], 'start_time': 1563260400, 'end_time': 1657287819.999794}
response=<Response [200]>
Found 5 entries
Retrieving data for ucb-sdb-ios-4 from 1657140407.479903 -> 1657287819.999794
Retrieving data for: post_body={'user': 'ucb-sdb-ios-4', 'key_list': ['analysis/cleaned_trip'], 'start_time': 1657140407.479903, 'end_time': 1657287819.999794}
response=<Response [200]>
Found 1 entries
Retrieving data for ucb-sdb-ios-4 from 1563260400 -> 1657287820.047015
Retrieving data for: post_body={'user': 'ucb-sdb-io

         dict_keys(['trip_id', 'trip_id_base', 'trip_run', 'start_ts', 'end_ts', 'duration', 'eval_common_trip_id', 'eval_role', 'eval_role_base', 'eval_role_run', 'evaluation_trip_ranges', 'background/battery', 'battery_df', 'background/location', 'background/filtered_location', 'location_df', 'filtered_location_df', 'background/motion_activity', 'motion_activity_df', 'statemachine/transition', 'transition_df'])
         fixed:POWER_CONTROL_6 MAMFDC v/s MAHFDC power_control_0 3
Before filtering, trips = [('2019-06-21T07:54:10.435970-07:00', '2019-06-21T08:03:31.997930-07:00'), ('2019-06-21T09:54:40.040418-07:00', '2019-06-21T10:13:52.827565-07:00'), ('2019-06-21T11:31:23.475080-07:00', '2019-06-21T12:11:49.996531-07:00'), ('2019-06-21T15:26:20.289034-07:00', '2019-06-21T15:35:36.994930-07:00'), ('2019-06-21T16:13:34.349776-07:00', '2019-06-21T16:34:40.058509-07:00')]
Filter range = 2019-11-19T08:08:06.766109-08:00 -> 2019-11-19T19:54:58.537710-08:00
After filtering, trips = []
Before 

Before filtering, trips = [('2019-06-21T07:54:10.435970-07:00', '2019-06-21T08:03:31.997930-07:00'), ('2019-06-21T09:54:40.040418-07:00', '2019-06-21T10:13:52.827565-07:00'), ('2019-06-21T11:31:23.475080-07:00', '2019-06-21T12:11:49.996531-07:00'), ('2019-06-21T15:26:20.289034-07:00', '2019-06-21T15:35:36.994930-07:00'), ('2019-06-21T16:13:34.349776-07:00', '2019-06-21T16:34:40.058509-07:00')]
Filter range = 2019-12-11T08:11:26.774655-08:00 -> 2019-12-11T20:08:29.363970-08:00
After filtering, trips = []
Before filtering, trips = [('2019-06-21T07:54:10.435970-07:00', '2019-06-21T08:03:31.997930-07:00'), ('2019-06-21T09:54:40.040418-07:00', '2019-06-21T10:13:52.827565-07:00'), ('2019-06-21T11:31:23.475080-07:00', '2019-06-21T12:11:49.996531-07:00'), ('2019-06-21T15:26:20.289034-07:00', '2019-06-21T15:35:36.994930-07:00'), ('2019-06-21T16:13:34.349776-07:00', '2019-06-21T16:34:40.058509-07:00')]
Filter range = 2019-12-11T08:12:44.752437-08:00 -> 2019-12-11T10:53:44.995113-08:00
After filt

#### inferred view random forest

In [ ]:
rfv_la   = eapv.create_analysed_view(pv_la, "http://localhost:8080", "analysis/recreated_location", "analysis/cleaned_trip", "analysis/inferred_section")
rfv_sj   = eapv.create_analysed_view(pv_sj, "http://localhost:8080", "analysis/recreated_location", "analysis/cleaned_trip", "analysis/inferred_section")
rfv_ucb  = eapv.create_analysed_view(pv_ucb, "http://localhost:8080", "analysis/recreated_location", "analysis/cleaned_trip", "analysis/inferred_section")

#### inferred view GIS

In [ ]:
gisv_la   = eapv.create_analysed_view(pv_la, "http://localhost:8080", "analysis/recreated_location", "analysis/cleaned_trip", "analysis/inferred_section")
gisv_sj   = eapv.create_analysed_view(pv_sj, "http://localhost:8080", "analysis/recreated_location", "analysis/cleaned_trip", "analysis/inferred_section")
gisv_ucb  = eapv.create_analysed_view(pv_ucb, "http://localhost:8080", "analysis/recreated_location", "analysis/cleaned_trip", "analysis/inferred_section")

# Results 

#### Raw data

In [ ]:
get_binary_raw_data('ios', [pv_la, pv_sj, pv_ucb], RBMM)

In [ ]:
get_binary_raw_data('android', [pv_la, pv_sj, pv_ucb], RBMM)

In [ ]:
display_f_score('ios', [pv_la, pv_sj, pv_ucb], RBMM)

In [ ]:
display_f_score('android', [pv_la, pv_sj, pv_ucb], RBMM)

In [ ]:
get_raw_cm('ios', [pv_la, pv_sj, pv_ucb])

In [ ]:
get_raw_cm('android',[pv_la, pv_sj, pv_ucb] )

#### Cleaned data

In [138]:
get_binary_raw_data('ios', [cv_la, cv_sj, cv_ucb], CBMM)

\begin{tabular}{lrrrr}
Title & \multicolumn{4}{r}{ios\_HAHFDC} \\
Mode & WALKING & CYCLING & AUTOMOTIVE & INVALID \\
Classifier &  &  &  &  \\
TP & 16774 & 54234 & 860146 & 81233 \\
FP & 13068 & 2083 & 82256 & 3747 \\
FN & 8227 & 5790 & 5997 & 0 \\
TN & 994332 & 970293 & 84003 & 947422 \\
\end{tabular}



AssertionError:  
                ERROR, NEGATIVE LEFTOVER OF -27.387164662497526, NEED TO INVESTIGATE
                sensed distance:   	 56563.48955448045
                computed distance: 	 56590.87671914295
                mode:              	 INVALID
                                      

In [139]:
get_binary_raw_data('android', [cv_la, cv_sj, cv_ucb], CBMM)

\begin{tabular}{lrrrr}
Title & \multicolumn{4}{r}{ios\_HAHFDC} \\
Mode & WALKING & CYCLING & AUTOMOTIVE & INVALID \\
Classifier &  &  &  &  \\
TP & 7881 & 18421 & 449599 & 3081 \\
FP & 468 & 404 & 2994 & 0 \\
FN & 781 & 5 & 0 & 0 \\
TN & 470638 & 460938 & 27176 & 476689 \\
\end{tabular}

\begin{tabular}{lrrrr}
Title & \multicolumn{4}{r}{ios\_HAHFDC} \\
Mode & WALKING & CYCLING & AUTOMOTIVE & INVALID \\
Classifier &  &  &  &  \\
TP & 25809 & 47994 & 799460 & 85853 \\
FP & 4310 & 412 & 105733 & 1691 \\
FN & 22738 & 543 & 3680 & 0 \\
TN & 933221 & 937130 & 77205 & 898535 \\
\end{tabular}

\begin{tabular}{lrrrr}
Title & \multicolumn{4}{r}{ios\_HAHFDC} \\
Mode & WALKING & CYCLING & AUTOMOTIVE & INVALID \\
Classifier &  &  &  &  \\
TP & 15615 & 37677 & 607326 & 7279 \\
FP & 2681 & 964 & 4751 & 43532 \\
FN & 87 & 520 & 44042 & 0 \\
TN & 694165 & 673386 & 56428 & 661738 \\
\end{tabular}



In [140]:
display_f_score('ios', [cv_la, cv_sj, cv_ucb], CBMM)

AssertionError:  
                ERROR, NEGATIVE LEFTOVER OF -27.387164662497526, NEED TO INVESTIGATE
                sensed distance:   	 56563.48955448045
                computed distance: 	 56590.87671914295
                mode:              	 INVALID
                                      

In [141]:
display_f_score('android', [cv_la, cv_sj, cv_ucb], CBMM)

([('INVALID', 1.0),
  ('AUTOMOTIVE', 0.9967),
  ('WALKING', 0.9265),
  ('CYCLING', 0.989)],
 [('INVALID', 0.9902),
  ('WALKING', 0.6562),
  ('AUTOMOTIVE', 0.936),
  ('CYCLING', 0.9901)],
 [('INVALID', 0.2506),
  ('WALKING', 0.9186),
  ('AUTOMOTIVE', 0.9614),
  ('CYCLING', 0.9807)])

In [142]:
get_raw_cm('ios', [cv_la, cv_sj, cv_ucb])

\begin{tabular}{lrrrrrrrr}
 & WALKING & BICYCLING & ESCOOTER & CAR & BUS & LIGHT_RAIL & TRAIN & NO_GT \\
sensed_mode &  &  &  &  &  &  &  &  \\
WALKING & nan & nan & nan & nan & nan & nan & nan & nan \\
RUNNING & nan & nan & nan & nan & nan & nan & nan & nan \\
CYCLING & nan & nan & nan & nan & nan & nan & nan & nan \\
AUTOMOTIVE & nan & nan & nan & nan & nan & nan & nan & nan \\
\end{tabular}



KeyError: 'mode'

In [143]:
get_raw_cm('android', [cv_la, cv_sj, cv_ucb] )

\begin{tabular}{lrrrrrrrr}
 & WALKING & BICYCLING & ESCOOTER & CAR & BUS & LIGHT_RAIL & TRAIN & NO_GT \\
sensed_mode &  &  &  &  &  &  &  &  \\
WALKING & nan & nan & nan & nan & nan & nan & nan & nan \\
CYCLING & nan & nan & nan & nan & nan & nan & nan & nan \\
AUTOMOTIVE & nan & nan & nan & nan & nan & nan & nan & nan \\
\end{tabular}

\begin{tabular}{lrrrrrrrr}
 & WALKING & BICYCLING & ESCOOTER & CAR & BUS & LIGHT_RAIL & TRAIN & NO_GT \\
sensed_mode &  &  &  &  &  &  &  &  \\
WALKING & nan & nan & nan & nan & nan & nan & nan & nan \\
CYCLING & nan & nan & nan & nan & nan & nan & nan & nan \\
AUTOMOTIVE & nan & nan & nan & nan & nan & nan & nan & nan \\
\end{tabular}

\begin{tabular}{lrrrrrrrr}
 & WALKING & BICYCLING & ESCOOTER & CAR & BUS & LIGHT_RAIL & TRAIN & NO_GT \\
sensed_mode &  &  &  &  &  &  &  &  \\
WALKING & nan & nan & nan & nan & nan & nan & nan & nan \\
CYCLING & nan & nan & nan & nan & nan & nan & nan & nan \\
AUTOMOTIVE & nan & nan & nan & nan & nan & nan & nan & nan \

#### Random Forrest

In [ ]:
get_rf_binary('ios')

In [ ]:
get_rf_binary('android')

In [ ]:
display_f_score('ios', [rfv_la, rfv_sj, rfv_ucb], IBMM)

In [ ]:
display_f_score('android', [rfv_la, rfv_sj, rfv_ucb], IBMM)

In [ ]:
get_rf_cm('ios', IBMM)

In [ ]:
get_rf_cm('android')

#### GIS

In [ ]:
get_rf_binary('ios', [gisv_la, gisv_sj, gisv_ucb])

In [ ]:
get_rf_binary('android', [gisv_la, gisv_sj, gisv_ucb])

In [ ]:
display_f_score('ios', [gisv_la, gisv_sj, gisv_ucb], IBMM)

In [ ]:
display_f_score('android', [gisv_la, gisv_sj, gisv_ucb], IBMM)

In [ ]:
get_rf_cm('ios')

In [ ]:
get_rf_cm('android')